In [23]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [24]:
import pandas as pd
import plotly.express as px
import src.Prophet as Prophet
from config.config import ESTACIONS_DIR, OBSERVACIONS_DIR, OBSERVACIONS_FILTRAT_DIR
import plotly.graph_objects as go
from pathlib import Path
import multiprocessing
from joblib import Parallel, delayed
import itertools
import numpy as np

In [25]:
estacions = pd.read_csv(ESTACIONS_DIR, index_col=5)
estacions.head()

Estació   UTM X    UTM Y  ID amunt_em
nom                                                                 
a01                 Aforament - Abrera  409650  4596023   1       no
a02  Aforament - Anglès (riera d'Osor)  469379  4645530   2       si
a03              Aforament - Balsareny  407058  4634787   3       no
a04          Aforament - Berga (Olvan)  407241  4659812   4       no
a05     Aforament - Boadella d'Empordà  488441  4686953   5       no

In [26]:
#Estacions correctes parcialment o totalment

for observacions_filtrat_path in list(OBSERVACIONS_FILTRAT_DIR.glob("*.csv"))[:10]:

    name_file = observacions_filtrat_path.name
    nom = name_file.replace('.csv', '')
    
    estacio = estacions.loc[nom]['Estació']
    observacions_filtrat = pd.read_csv(observacions_filtrat_path)
    observacions = pd.read_csv(Path(OBSERVACIONS_DIR, name_file))


    fig = go.Figure()
    fig.add_trace(go.Scatter(x=observacions["Date"], y=observacions["Flow"], name="Observacions", mode="lines"))
    fig.add_trace(go.Scatter(x=observacions_filtrat["Date"], y=observacions_filtrat["Flow"], name="Observacions filtrats", mode="lines"))
    fig.update_layout(
        title=estacio + '--' + nom
    )    
    fig.show()


In [27]:
estacions_filtrades = list(map(lambda path: path.name, OBSERVACIONS_FILTRAT_DIR.glob("*.csv")))
totes_estacions = list(map(lambda path: path.name, OBSERVACIONS_DIR.glob("*.csv")))
estacions_descartades = set(totes_estacions) - set(estacions_filtrades)
estacions_descartades

{'a02.csv',
 'a06.csv',
 'a10.csv',
 'a14.csv',
 'a15.csv',
 'a27.csv',
 'a32.csv',
 'a56.csv',
 'a63.csv',
 'a64.csv'}

In [30]:
#for each element of estacions_descartades, get the file in OBSERVACIONS_DIR and plot it
for nom_estacio in estacions_descartades:
    observacions = pd.read_csv(Path(OBSERVACIONS_DIR, nom_estacio))
    estacio = estacions.loc[nom_estacio.replace('.csv', '')]['Estació']
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=observacions["Date"], y=observacions["Flow"], name="Observacions", mode="lines"))
    fig.update_layout(
        title=estacio + '--' + nom_estacio
    )    
    fig.show()

In [29]:
#https://towardsdatascience.com/anomaly-detection-time-series-4c661f6f165f
#https://facebook.github.io/prophet/docs/seasonality,_holiday_effects,_and_regressors.html
#https://github.com/uber/orbit
#https://towardsdatascience.com/tods-detecting-outliers-from-time-series-data-2d4bd2e91381
#sarima


def errors_from_file(file, **kwargs):

    observacio_filtrada_df = pd.read_csv(file).rename(columns = {'Date': 'ds', 'Flow': 'y'})
    prophet_model = Prophet.Prophet(observacio_filtrada_df, **kwargs)
    
    nash = prophet_model.nash()
    pbias = prophet_model.pbias()

    return nash, pbias


def errors_from_config(**kwargs):

    num_cores = multiprocessing.cpu_count()
    nash, pbias = zip(*Parallel(n_jobs=num_cores)(delayed(errors_from_file)(file, **kwargs) for file in OBSERVACIONS_FILTRAT_DIR.glob("*.csv")))

    return sum(nash) / len(nash), sum(pbias) / len(pbias)

def hyperparameter_opt(fitted_model, **kwargs):
    
    nash, pbias = errors_from_config(fitted_model, **kwargs)
    return nash, pbias
